In [2]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from sqlalchemy import create_engine
from sklearn import preprocessing
import mysql.connector
from pandas import DataFrame

# data

In [4]:
Triples_target_final = pd.read_csv("Triples_target_final.tsv", sep='\t')
Triples_target_final = Triples_target_final.drop(["Unnamed: 0"],axis=1)

In [5]:
triplets_total = pd.read_csv('triplets_total.csv', sep=';')

In [7]:
triplets_total = triplets_total.drop_duplicates()

In [11]:
disease_id = triplets_total["disease_no_PwB"]

In [12]:
def convert(lista):
    return tuple(i for i in lista)

In [13]:
# Driver function
lista = disease_id
print(convert(lista))
list_disease_id = convert(lista)

('C0018802', 'C0018802', 'C0004238', 'C0011881', 'C0001206', 'C0020649', 'C0024586', 'C0010674', 'C0011881', 'C0004238', 'C0003962', 'C0013604', 'C0020428', 'C0020473', 'C0018801', 'C0004096', 'C0009324', 'C0010346', 'C0011849', 'C0020598', 'C0020626', 'C0024141', 'C0026769', 'C0028754', 'C0029456', 'C0029458', 'C0015371', 'C0020598', 'C0035086', 'C0011881', 'C0002395', 'C0026769', 'C0020598', 'C0020626', 'C0029456', 'C0029458', 'C0020598', 'C0020626', 'C0020598', 'C0020626', 'C0035086', 'C0003862', 'C0003873', 'C0004153', 'C0004604', 'C0009443', 'C0026764', 'C0001144', 'C0001261', 'C0003175', 'C0006277', 'C0006309', 'C0010674', 'C0011581', 'C0018081', 'C0023860', 'C0027404', 'C0030193', 'C0016053', 'C0184567', 'C0242422', 'C0600177', 'C1621958', 'C0027051', 'C0028754', 'C0038454', 'C0038454', 'C0036337', 'C0036341', 'C0042870', 'C0242422', 'C1739363', 'C0042847', 'C0162316', 'C0006114', 'C0033860', 'C0042847', 'C0085682', 'C0184567', 'C0242422', 'C0026769', 'C0030567', 'C0036341', 'C0

In [20]:
dis_gen = f'''SELECT disease_id, gene_id FROM disnet_biolayer.disease_gene
where sio_id != 'SIO_001120'
and sio_id != 'NO_CURATED'
and disease_id IN {list_disease_id}
;'''

In [21]:
dis_gen=pd.read_sql(dis_gen, con=disnet_db_ares)

In [23]:
dis_gen_num_gen = dis_gen.groupby(['disease_id']).count()

In [25]:
dis_gen_num_gen = dis_gen_num_gen.reset_index()

In [27]:
dis_gen_num_gen["gene_id"].mean()

228.91780821917808

In [28]:
dis_gen_num_gen["gene_id"].describe()

count      73.000000
mean      228.917808
std       301.082480
min         1.000000
25%        14.000000
50%        79.000000
75%       392.000000
max      1369.000000
Name: gene_id, dtype: float64

In [ ]:
#### pw via gene

In [31]:
dis_gen_pw = f'''
SELECT dg.disease_id,gp.pathway_id
        FROM disnet_biolayer.disease_gene dg 
    JOIN disnet_biolayer.disease ds ON ds.disease_id = dg.disease_id
    JOIN disnet_biolayer.tmp_gene_pathway gp ON gp.gene_id = dg.gene_id
    where dg.disease_id in {list_disease_id}
'''

In [32]:
dis_gen_pw=pd.read_sql(dis_gen_pw, con=disnet_db_ares)

In [33]:
dis_gen_pw = dis_gen_pw.groupby(['disease_id']).count()

In [34]:
dis_gen_pw = dis_gen_pw.reset_index()

In [36]:
dis_gen_pw["pathway_id"].mean()

766.2361111111111

In [ ]:
#### pw direct

In [ ]:
dis_path_direct = pd.read_csv('disease_pathway.tsv', sep='\t')

In [59]:
triplets_total_fil = triplets_total.drop(["disease_PwB","drug_id"],axis=1)

In [60]:
triplets_total_fil = triplets_total_fil.rename(columns={"disease_no_PwB": "disease_id"})

In [61]:
dr_pw = triplets_total_fil.merge(dis_path_direct,on="disease_id",how= "inner")

In [63]:
dr_pw = dr_pw.groupby(['disease_id']).count()

In [64]:
dr_pw = dr_pw.reset_index()

In [65]:
dr_pw["pathway_id"].mean()

6.4

In [ ]:
### drug

In [46]:
drug = f'''SELECT disease_id,drug_id FROM disnet_drugslayer.drug_disease
where disease_id in {list_disease_id}'''

In [47]:
drug=pd.read_sql(drug, con=disnet_db_ares)

In [49]:
drug = drug.groupby(['disease_id']).count()

In [51]:
drug = drug.reset_index()

In [52]:
drug["drug_id"].mean()

441.88607594936707

In [ ]:
### sintomas

In [53]:
sint = f'''SELECT DISTINCT
        ds.disease_id,s.cui as symptom 
        FROM disnet_biolayer.disease ds 
            JOIN edsssdb.layersmappings lm on ds.disease_id = lm.cui
            JOIN edsssdb.disease_symptom dsy ON lm.disnet_id = dsy.disease_id
            JOIN edsssdb.symptom s ON dsy.cui = s.cui
       where ds.disease_id in {list_disease_id}
'''

In [54]:
sint_all=pd.read_sql(sint, con=disnet_db_ares)

In [55]:
sint_all = sint_all.groupby(['disease_id']).count()

In [56]:
sint_all = sint_all.reset_index()

In [57]:
sint_all["symptom"].mean()

76.81333333333333